In [329]:
#!g1.1
from sklearn.preprocessing import LabelEncoder
import transformers
import torch
import nltk
import numpy as np
import pandas as pd

In [330]:
#!g1.1
df = pd.read_json('arxiv-metadata-oai-snapshot.json', lines = True)

In [331]:
#!g1.1
df.head(5)

id           submitter  \
0  0704.0001      Pavel Nadolsky   
1  0704.0002        Louis Theran   
2  0704.0003         Hongjun Pan   
3  0704.0004        David Callan   
4  0704.0005  Alberto Torchinsky   

                                             authors  \
0  C. Bal\'azs, E. L. Berger, P. M. Nadolsky, C.-...   
1                    Ileana Streinu and Louis Theran   
2                                        Hongjun Pan   
3                                       David Callan   
4           Wael Abu-Shammala and Alberto Torchinsky   

                                               title  \
0  Calculation of prompt diphoton production cros...   
1           Sparsity-certifying Graph Decompositions   
2  The evolution of the Earth-Moon system based o...   
3  A determinant of Stirling cycle numbers counts...   
4  From dyadic $\Lambda_{\alpha}$ to $\Lambda_{\a...   

                                  comments  \
0  37 pages, 15 figures; published version   
1    To appear in Graphs and Combinatorics   
2                      23 pages, 3 figures   
3                                 11 pages   
4                                     None   

                                 journal-ref                         doi  \
0                   Phys.Rev.D76:013009,2007  10.1103/PhysRevD.76.013009   
1                                       None                        None   
2                                       None                        None   
3                                       None                        None   
4  Illinois J. Math. 52 (2008) no.2, 681-689                        None   

          report-no       categories  \
0  ANL-HEP-PR-07-12           hep-ph   
1              None    math.CO cs.CG   
2              None   physics.gen-ph   
3              None          math.CO   
4              None  math.CA math.FA   

                                             license  \
0                                               None   
1  http://arxiv.org/licenses/nonexclusive-distrib...   
2                                               None   
3                                               None   
4                                               None   

                                            abstract  \
0    A fully differential calculation in perturba...   
1    We describe a new algorithm, the $(k,\ell)$-...   
2    The evolution of Earth-Moon system is descri...   
3    We show that a determinant of Stirling cycle...   
4    In this paper we show how to compute the $\L...   

                                            versions update_date  \
0  [{'version': 'v1', 'created': 'Mon, 2 Apr 2007...  2008-11-26   
1  [{'version': 'v1', 'created': 'Sat, 31 Mar 200...  2008-12-13   
2  [{'version': 'v1', 'created': 'Sun, 1 Apr 2007...  2008-01-13   
3  [{'version': 'v1', 'created': 'Sat, 31 Mar 200...  2007-05-23   
4  [{'version': 'v1', 'created': 'Mon, 2 Apr 2007...  2013-10-15   

                                      authors_parsed  
0  [[Balázs, C., ], [Berger, E. L., ], [Nadolsky,...  
1           [[Streinu, Ileana, ], [Theran, Louis, ]]  
2                                 [[Pan, Hongjun, ]]  
3                                [[Callan, David, ]]  
4  [[Abu-Shammala, Wael, ], [Torchinsky, Alberto, ]]

In [332]:
#!g1.1
str(df[10:11]['categories']).split()[1]

'math.NT'

In [333]:
#!g1.1
def get_tag(row):
    try:
        return str(row).split()[0].split('.')[0]
    except Exception:
        pass
    

df['tag'] = df['categories'].apply(lambda x: get_tag(x))
df.head(5)

id           submitter  \
0  0704.0001      Pavel Nadolsky   
1  0704.0002        Louis Theran   
2  0704.0003         Hongjun Pan   
3  0704.0004        David Callan   
4  0704.0005  Alberto Torchinsky   

                                             authors  \
0  C. Bal\'azs, E. L. Berger, P. M. Nadolsky, C.-...   
1                    Ileana Streinu and Louis Theran   
2                                        Hongjun Pan   
3                                       David Callan   
4           Wael Abu-Shammala and Alberto Torchinsky   

                                               title  \
0  Calculation of prompt diphoton production cros...   
1           Sparsity-certifying Graph Decompositions   
2  The evolution of the Earth-Moon system based o...   
3  A determinant of Stirling cycle numbers counts...   
4  From dyadic $\Lambda_{\alpha}$ to $\Lambda_{\a...   

                                  comments  \
0  37 pages, 15 figures; published version   
1    To appear in Graphs and Combinatorics   
2                      23 pages, 3 figures   
3                                 11 pages   
4                                     None   

                                 journal-ref                         doi  \
0                   Phys.Rev.D76:013009,2007  10.1103/PhysRevD.76.013009   
1                                       None                        None   
2                                       None                        None   
3                                       None                        None   
4  Illinois J. Math. 52 (2008) no.2, 681-689                        None   

          report-no       categories  \
0  ANL-HEP-PR-07-12           hep-ph   
1              None    math.CO cs.CG   
2              None   physics.gen-ph   
3              None          math.CO   
4              None  math.CA math.FA   

                                             license  \
0                                               None   
1  http://arxiv.org/licenses/nonexclusive-distrib...   
2                                               None   
3                                               None   
4                                               None   

                                            abstract  \
0    A fully differential calculation in perturba...   
1    We describe a new algorithm, the $(k,\ell)$-...   
2    The evolution of Earth-Moon system is descri...   
3    We show that a determinant of Stirling cycle...   
4    In this paper we show how to compute the $\L...   

                                            versions update_date  \
0  [{'version': 'v1', 'created': 'Mon, 2 Apr 2007...  2008-11-26   
1  [{'version': 'v1', 'created': 'Sat, 31 Mar 200...  2008-12-13   
2  [{'version': 'v1', 'created': 'Sun, 1 Apr 2007...  2008-01-13   
3  [{'version': 'v1', 'created': 'Sat, 31 Mar 200...  2007-05-23   
4  [{'version': 'v1', 'created': 'Mon, 2 Apr 2007...  2013-10-15   

                                      authors_parsed      tag  
0  [[Balázs, C., ], [Berger, E. L., ], [Nadolsky,...   hep-ph  
1           [[Streinu, Ileana, ], [Theran, Louis, ]]     math  
2                                 [[Pan, Hongjun, ]]  physics  
3                                [[Callan, David, ]]     math  
4  [[Abu-Shammala, Wael, ], [Torchinsky, Alberto, ]]     math

/kernel/lib/python3.8/site-packages/ml_kernel/ignored_keyboard_interrupt.py:16: UserWarning: State committing stage cannot be interrupted. Please wait.
  warnings.warn(self._warn_message)


In [390]:
#!g1.1
labels = []
for index, row in df.iterrows():
    labels.append(row['tag'])
    

In [391]:
#!g1.1
map_labels = dict()
for label in labels:
    if label in map_labels:
        map_labels[label] += 1
    else:
        map_labels[label] = 1 

In [397]:
#!g1.1
map_labels

{'hep-ph': 120410,
 'math': 414977,
 'physics': 146186,
 'cond-mat': 276428,
 'gr-qc': 54599,
 'astro-ph': 266321,
 'hep-th': 96207,
 'hep-ex': 20735,
 'nlin': 17315,
 'q-bio': 23287,
 'quant-ph': 88923,
 'cs': 338681,
 'nucl-th': 30599,
 'math-ph': 28805,
 'hep-lat': 16623,
 'nucl-ex': 10500,
 'q-fin': 9131,
 'stat': 37132,
 'eess': 27531,
 'econ': 3904,
 'acc-phys': 46,
 'adap-org': 306,
 'alg-geom': 1209,
 'ao-sci': 13,
 'atom-ph': 68,
 'bayes-an': 11,
 'chao-dyn': 1770,
 'chem-ph': 129,
 'cmp-lg': 894,
 'comp-gas': 140,
 'dg-ga': 562,
 'funct-an': 320,
 'mtrl-th': 165,
 'patt-sol': 452,
 'plasm-ph': 28,
 'q-alg': 1177,
 'solv-int': 844,
 'supr-con': 69}

In [398]:
#!g1.1
dict_label = {'math': 4,
              'physics': 5,
              'q-bio': 6,
              'cs': 1,
              'q-fin': 7,
              'stat': 8,
              'eess': 3,
              'econ': 2}

In [399]:
#!g1.1
new_map_labels = dict()
for key, value in map_labels.items():
    if key in dict_label:
        new_map_labels[key] = value   

In [400]:
#!g1.1
new_map_labels

{'math': 414977,
 'physics': 146186,
 'q-bio': 23287,
 'cs': 338681,
 'q-fin': 9131,
 'stat': 37132,
 'eess': 27531,
 'econ': 3904}

In [401]:
#!g1.1
sum_value = 0
for key, value in new_map_labels.items():
    sum_value += min(value, 8000) 
    new_map_labels[key] = min(value, 8000) 
sum_value

59904

In [405]:
#!g1.1 
small_df = pd.DataFrame()

for idx, row in df.iterrows():
    if row['tag'] in new_map_labels:
        
        if new_map_labels[row['tag']] > 0:
            new_map_labels[row['tag']] -= 1

            small_df = small_df.append(row, ignore_index=True)
            

In [406]:
#!g1.1
small_df.shape

(59904, 15)

In [407]:
#!g1.1
small_df["text"] = small_df["title"] + ". " + small_df["abstract"]
small_df["text"] = small_df["text"].map(lambda x : x.replace("\n", " "))
small_df["text"] = small_df["text"].str.lower()


In [428]:
#!g1.1
for idx, row in small_df.iterrows():
    row['categories'] = dict_label[row['tag']] - 1
    
small_df['label'] = small_df['categories']

In [435]:
#!g1.1
data = small_df[['text', 'label']]

In [440]:
#!g1.1
sum(data['label'] == 8)

0

In [409]:
#!g1.1
dict_label_map = dict()
for idx, row in small_df.iterrows():
    if row['tag'] in dict_label_map:
        dict_label_map[row['tag']] += 1
    else:
        dict_label_map[row['tag']] = 1

In [410]:
#!g1.1
dict_label_map

{'math': 8000,
 'physics': 8000,
 'q-bio': 8000,
 'cs': 8000,
 'q-fin': 8000,
 'stat': 8000,
 'eess': 8000,
 'econ': 3904}

In [441]:
#!g1.1
from sklearn.model_selection import train_test_split
train_data, test_data = train_test_split(data, test_size=0.2)
train_data, val_data = train_test_split(data, test_size=0.25)

In [442]:
#!g1.1
train_data.to_csv('train_data.csv', index=None)
val_data.to_csv('val_data.csv', index=None)
test_data.to_csv('test_data.csv', index=None)

In [414]:
#!g1.1
# тут датасфера не дает мне нормальной возможности работать с токенизатором, поэтому перейдем в другой ноутбук где и продолжим 